In [ ]:
#@title
# importing the required dependencies

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import os
import plotly.express as px
from scipy.stats import norm, gaussian_kde

In [ ]:
#@title
aggregate_2019 = pd.read_csv('total_aggregate-2019.csv',index_col='timeFrom')
aggregate_2020 = pd.read_csv('total_aggregate-2020.csv',index_col='timeFrom')

In [ ]:
#@title
total_aggregate = pd.concat([aggregate_2019,aggregate_2020],axis=1)*2

In [ ]:
#@title
min_val = total_aggregate.min().min()*0.8
max_val = total_aggregate.max().max()*1.2

(0.0, 582476.5533808257)

In [ ]:
#@title
def make_pdf(row,res=200):
  val = row.dropna().values
  bw =0.04
  kernel = gaussian_kde(val,bw_method=bw)
  space = np.linspace(min_val,max_val,res)
  prob = kernel.pdf(space)
  interval = (max_val-min_val)/res
  return pd.Series(prob*interval)



def make_cdf(row,res=400):
  prob = make_pdf(row,res)
  cumulative = prob.cumsum()
  
  return pd.Series(cumulative)

def make_discrete_cdf(row,minv=min_val,maxv=max_val,res=100):
  models = row.dropna().values
  space = np.linspace(minv,maxv,res)
  cumulative = [(value<models).sum() for value in space]
  cumulative = pd.Series(cumulative)
  return cumulative/cumulative.max()

In [ ]:
#@title



heatmap_dec = total_aggregate.apply(make_discrete_cdf,axis=1)
heatmap_dec.columns = np.linspace(min_val,max_val,100)

heatmap_dec_density = total_aggregate.apply(make_pdf,axis=1)
heatmap_dec_density.columns = np.linspace(min_val,max_val,200)



probability density

In [ ]:
#@title

import plotly.graph_objects as go


fig = go.Figure(data=go.Heatmap(
        x = heatmap_dec_density.index,
        y=  heatmap_dec_density.columns,
        z=heatmap_dec_density.T,
        colorscale='rdBu'))

fig.update_xaxes(type='date',title='time')
fig.update_yaxes(type='linear',title='consumption')
fig.update_layout(yaxis = {'tickfont': {'size': 7}})

fig.update_layout(height=600)
fig.show()

cumulative probabilitiy:

(notice that there is some undershoot)

In [ ]:
#@title
fig = go.Figure(data=go.Heatmap(
        x = heatmap_dec.index,
        y=  heatmap_dec.columns,
        z=heatmap_dec.T,
        colorscale='rdBu'))

fig.update_xaxes(type='date',title='time')
fig.update_yaxes(type='linear',title='consumption')
fig.update_layout(yaxis = {'tickfont': {'size': 7}})

fig.update_layout(height=600)
fig.show()

In [ ]:
#@title
by_effect = pd.read_csv('station_risk_consumption.csv',index_col='id')
by_effect = by_effect.drop('total',axis=0)

In [ ]:
#@title

fig = px.scatter(by_effect, x="consumption", y="effect_on_max",text=by_effect.index)
fig.update_traces(textposition='top center',textfont_size=10)
fig.show()

In [ ]:
#@title
by_effect.sort_values('ratio',ascending=False)

effect_on_max   consumption     ratio
id                                         
795        15.90625    4267.55625  0.003727
1053       32.21800    9631.00000  0.003345
1056       31.44000   12794.04000  0.002457
1047       13.71875    5677.25000  0.002416
1033     1407.75000  618777.00000  0.002275
...             ...           ...       ...
981        42.50000  123050.50000  0.000345
1063       13.40000   39462.65000  0.000340
675         3.42500   12077.15000  0.000284
974       220.00000  996521.00000  0.000221
1132       26.00000  117860.25000  0.000221

[307 rows x 3 columns]

In [ ]:
#@title
daily_maxes = pd.read_csv('daily_maxes.csv',index_col='timeFrom')
daily_maxes = daily_maxes.drop(columns='total')

daily_maxes.head()

4    11  ...  Energy Systems Jerusalem 1  HCN Main
timeFrom                ...                                      
1         1360.0  1798  ...                      2856.0      58.0
2         1183.0  1898  ...                      3037.2      68.0
3         1135.0  1658  ...                      2728.8      60.0
4          984.0  1786  ...                      1380.0      42.0
5          403.0  1208  ...                      1282.8      42.0

[5 rows x 307 columns]

In [ ]:
#@title
fig = go.Figure()
for col in daily_maxes.columns:
  fig.add_trace(go.Box(x=daily_maxes[col],name=col))

fig.update_yaxes(type='category',title='id')
fig.update_layout(height=800)
fig.show()

In [ ]:
#@title
by_std = daily_maxes.apply(np.std).sort_values(ascending=False)

In [ ]:
#@title
by_std

312     4243.991163
311     3843.490609
CAOL    2937.830209
242     2533.263416
50       959.228814
           ...     
794        2.647838
1052       2.371907
944        2.320540
568        1.063825
939        0.070343
Length: 307, dtype: float64

In [ ]:
#@title
import plotly.graph_objects as go

fig = go.Figure(go.Bar(
            x=by_std[::-1],
            y=by_std.index[::-1],
            orientation='h'))
fig.update_yaxes(type='category',title='consumption')
fig.update_layout(height=2000)
fig.show()